In [80]:
import geopandas as gpd
from shapely.geometry import MultiPoint, Point
from pprint import pprint
import numpy as np
from cartopy import crs
import hvplot.pandas
import hvplot.xarray
import geoviews as gv
import xarray as xr

gv.extension('bokeh', logo=False)

# check original elevation data

In [2]:
ds = xr.open_rasterio('../elevation/output.vrt')

z = ds.values
z = np.where(z==-9999, np.nan, z)
ds.values = z

epsg = int(ds.attrs['crs'][-4:])

g = ds.isel(band=0).hvplot.image(x='x',y='y', cmap='terrain',geo=True
                    , dynamic=True, rasterize=True, colorbar=True, alpha=1).options(clipping_colors={'NaN':'transparent'})

back = gv.WMTS('https://mt1.google.com/vt/lyrs=s&x={X}&y={Y}&z={Z}', name="GoogleMapsImagery" 
               , crs=crs.epsg(epsg))
# .redim( Longitude={'range':(ds.x.min(), ds.x.max())}, Latitude={'range':(ds.y.min(), ds.y.max())})

gall = (back*g).options(xlabel='', ylabel='')

In [4]:
p0 = np.array( [28150.57829278072313173, 11636.38226537326954713] )
p1 = np.array( [28304.03661753798587597, 11042.35004050644965901] )

e = (p1-p0)/np.linalg.norm(p1-p0)

po = p0 - 2200.0*e

def mkunitvecotr(th):
    ex = np.array( [1, 0] )
    th = th * np.pi / 180
    r = np.array( [[np.cos(th), -np.sin(th)],[np.sin(th), np.cos(th)]])
    return np.dot( r, ex.T)

deg = np.degrees( np.arctan2(e[1], e[0]) ) - 3

# thx = 10.5 - 90 
thx = deg
exi = mkunitvecotr(thx-90)
eeta = mkunitvecotr(thx)

Lx, Ly = 9000, 3000
pathxi = np.c_[po, po + exi*Lx].T
patheta = np.c_[po, po + eeta*Ly].T

# drawing using geoviews
l1 = gv.Path(pathxi, crs=crs.epsg(epsg)).options(line_width=2)
l2 = gv.Path(patheta, crs=crs.epsg(epsg)).options(line_width=2)

out = l1*l2

# back = gv.WMTS( 'https://mt1.google.com/vt/lyrs=s&x={X}&y={Y}&z={Z}', name="GoogleMapsImagery")
# g1 = gdfsect.hvplot.points(dynamic=True, geo=True, project=True, crs=crs.epsg(epsg))

gg = out * gall
gg

:DynamicMap   []
   :Overlay
      .Path.I  :Path   [Longitude,Latitude]
      .Path.II :Path   [Longitude,Latitude]
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [x,y]   (value)

# make geopandas dataframe 

In [81]:
d=2.5
Lx/d * Ly/d

4320000.0

In [82]:

def getz(pl, z, dx, dy, xOrigin, yOrigin, xmax, xmin, ymax, ymin):
    
    if pl[0]>xmax or pl[0]<xmin or pl[1]>ymax or pl[1]<ymin : return float(9999)
    
    xind = np.floor( (pl[0] - xOrigin)/dx ).astype(int) 
    yind = np.floor( (yOrigin - pl[1])/dy ).astype(int) 
    
    return z[yind, xind]

In [83]:
ds = xr.open_rasterio('../elevation/output.vrt')
z = ds.values
z = np.where(z==-9999, float(9999), z)
ds.values = z

# get raster properties
dy, dx = ds.res
xOrigin =ds.x.values[0] - 0.5*dx
yOrigin =ds.y.values[0] + 0.5*dy
ynum = ds.shape[1]
xnum = ds.shape[2]
z = ds.values[0]
xmax = ds.x.values.max()
xmin = ds.x.values.min()
ymax = ds.y.values.max()
ymin = ds.y.values.min()

In [84]:
%%time
geo = []
iarr = []
jarr = []
zb = []

dxcal, dycal = 2.5, 2.5
for i in range(int(Lx/dxcal)):
    for j in range( int(Ly/dycal) ):
        p = po + exi*dxcal*i + eeta*dycal*j
        xx = Point(p.flatten())
        geo.append( Point(p.flatten()) )
        zb.append( getz(p, z, dx, dy, xOrigin, yOrigin, xmax, xmin, ymax, ymin) )
        iarr.append(i)
        jarr.append(j)

Wall time: 1min 39s


In [85]:
gdf= gpd.GeoDataFrame({'geometry':geo, 'zb': zb, 'I':iarr, 'J':jarr})
gdf.crs = {'init': 'epsg:'+str(epsg)}

# dout = gdf.to_file("cal_Cartesian.geojson", driver='GeoJSON')
# del dout

# make xarray 

In [86]:
ni = gdf.iloc[-1].squeeze()['I'] + 1
nj = gdf.iloc[-1].squeeze()['J'] + 1

xc, yc, zc = [], [], []
for ind in range(ni):
    gdfp = gdf[gdf['I'] == ind]
    npgeo = np.array([ np.array( g.coords[:][0] ) for g in gdfp['geometry'].values ])
    xc.append( npgeo[:,0] )
    yc.append( npgeo[:,1] )
    zc.append( gdfp['zb'].values )

In [87]:
xc = np.array(xc)
yc = np.array(yc)
zc = np.array(zc)

In [88]:
ds = xr.Dataset({'elevation': (['x','y'], zc) }, coords={'xc': (('x', 'y'), xc), 'yc': (('x', 'y'), yc)}
               , attrs= {'crs':'+init=epsg:' + str(epsg)})

In [89]:
ds.elevation.values[ ds.elevation.values > 9000 ] = np.nan
# ds.elevation.values[ ds.elevation.values < -10 ] = np.nan
out1 = ds.hvplot.quadmesh( 'xc','yc',z='elevation'
                          , geo=True, frame_height=400, frame_width=500, project=False, tiles='OSM'
                          , rasterize=True, dynamic=True, cmap='jet',colorbar=True, alpha=0.1  #, clim=(-5,10)
                         )
#.redim.range(elevation=(-5,10))
# .opts(clipping_colors={'max':'red'})

# .options(clipping_colors={'max':'transparent'}) #.redim.range(elevation=(-1,10))

In [75]:
out1

:DynamicMap   []
   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Image.I :Image   [xc,yc]   (elevation)

In [90]:
ds.elevation.values[ np.isnan(ds.elevation.values) ] = float(9999)

In [91]:
ds

<xarray.Dataset>
Dimensions:    (x: 3600, y: 1200)
Coordinates:
    xc         (x, y) float64 2.76e+04 2.76e+04 2.76e+04 ... 1.938e+04 1.938e+04
    yc         (x, y) float64 1.377e+04 1.376e+04 ... 9.04e+03 9.038e+03
Dimensions without coordinates: x, y
Data variables:
    elevation  (x, y) float64 9.999e+03 9.999e+03 ... 9.999e+03 9.999e+03
Attributes:
    crs:      +init=epsg:6674

In [92]:
out = ds.to_netcdf('zb.nc')
del out

In [1]:
3600* 1200

4320000